# DEPRECATED

## This method of interacting with the Capella API has been deprecated in favor of the [Capella Console Client](https://github.com/capellaspace/console-client)

# Capella API: Search Open Data

This example defines several geographic region queries
to get you started using Capella Open Data.
Once you have the query results you want, you can borrow code from
the Capella-API-search-order-download-example notebook to get the data

In [42]:
# Required libraries:
# requests
# json
# urllib
# folium

In [11]:
!pip install urllib  # skip this if library is already installed

Looking in indexes: https://packages.corp.capellaspace.com, https://packages.corp.capellaspace.com/pypi/simple/
Looking in links: https://packages.corp.capellaspace.com/pypi/simple/
ERROR: Could not find a version that satisfies the requirement urllib (from versions: none)
ERROR: No matching distribution found for urllib

[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: pip install --upgrade pip


### Setup

In [3]:
import requests
import json

# Capella API endpoints
URL = 'https://api.capellaspace.com'
token = '/token'
catsearch = '/catalog/search'

# we're going to limit queries to the data accessable 
# within the open data program
data_collection = ["capella-open-data"]

Your username and password must be saved in a .json file named 'credentials.json' and formatted as follows.

{"username": "yourusername","password": "xxxxxxxxx"}

In [47]:
#Load username and password
with open('../credentials.json') as f:
    data = json.load(f)
    username = data['username']
    password = data['password']
username

'david.hemphill@capellaspace.com'

In [ ]:
#Authenticate and get a token
r = requests.post(URL + token, 
                  headers = {'Content-Type': 'application/x-www-form-urlencoded'}, auth=(username,password))

accesstoken = r.json()["accessToken"]
headers = {'Authorization':'Bearer ' + accesstoken}
headers

### Geographic region query example (not used by default)

In [6]:
# Change this to use a custom AOI
# This is turned off by default, but can be enabled in the query below
aoi = {
        "type": "Polygon",
        "coordinates": [
          [
            [
              181.7578125,
              -46.31658418182218
            ],
            [
              181.40625,
              -1.0546279422758742
            ],
            [
              146.6015625,
              57.51582286553883
            ],
            [
              124.8046875,
              41.77131167976407
            ],
            [
              112.5,
              18.979025953255267
            ],
            [
              90,
              32.84267363195431
            ],
            [
              77.6953125,
              9.795677582829743
            ],
            [
              93.8671875,
              -34.59704151614416
            ],
            [
              150.46875,
              -54.162433968067795
            ],
            [
              181.7578125,
              -46.31658418182218
            ]
          ]
        ]
      }

### POST Search

In [7]:
# Post search filters
filters = {
  # "intersects": aoi,  # uncomment to filter by geography
  "limit": 1000, # overwrite the default pagination limit of 10, adjust as necessary
  "collections": data_collection, #["capella-open-data"], # specify the desired collection  "sentinel-s1-l2"
  "sortby": "properties.datetime"
}

headers = {'Content-Type': 'application/json',
  'Accept': 'application/geo+json', 'Authorization':'Bearer ' + accesstoken}
r = requests.post(URL + catsearch, json=filters, headers=headers)

jresult = r.json()
print("Items Found: %s" % jresult['context']['matched'])

Items Found: 1009


In [12]:
# Display the results on a folium map
import folium
f = folium.Figure(width=700, height=500)  #sizing for the cell
m = folium.Map(location=(0,0),zoom_start=1).add_to(f) # create and initialize the map
folium.GeoJson(r.text).add_to(m) # add the bbox geometries to the map
m